In [1]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn import preprocessing
from sklearn.metrics import classification_report, roc_auc_score
from sklearn.model_selection import StratifiedKFold
#from sklearn.model_selection import cross_val_score, ShuffleSplit
#from sklearn.model_selection import StratifiedShuffleSplit
#from sklearn.model_selection import train_test_split
from xgboost import XGBClassifier
#from imblearn.combine import SMOTEENN
#from imblearn.over_sampling import SMOTE
#from imblearn.over_sampling import RandomOverSampler, SMOTE
#from imblearn.ensemble import EasyEnsembleClassifier
from tensorflow import random
from tensorflow import keras
#from sklearn.ensemble import StackingClassifier
#from sklearn.metrics import make_scorer
from sklearn.feature_selection import SelectFromModel

In [2]:
def data_processing(X_train, X_test):
    scaler = preprocessing.StandardScaler()
    train_scale = scaler.fit_transform(X_train)
    test_scale = scaler.transform(X_test)
    return train_scale, test_scale

# get a list of models to evaluate

# build cnn_model

def create_model(shape):
    np.random.seed(42)
    random.set_seed(42)
    optimizer = keras.optimizers.SGD()
    cnn_model = keras.models.Sequential()
    cnn_model.add(keras.layers.Conv1D(256,3,activation='tanh',input_shape=(shape,1)))
    cnn_model.add(keras.layers.Dropout(0.2))
    cnn_model.add(keras.layers.Conv1D(128,3,activation='tanh'))
    cnn_model.add(keras.layers.Dropout(0.2))
    cnn_model.add(keras.layers.Flatten())
    cnn_model.add(keras.layers.Dense(64,activation='tanh'))
    cnn_model.add(keras.layers.Dense(1,activation='sigmoid'))    
    cnn_model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return cnn_model  

#cnn_model = keras.wrappers.scikit_learn.KerasClassifier(build_fn=create_model)

def get_models():
    models = dict()
    models['lr'] = LogisticRegression(solver='newton-cg', max_iter=500)
    #models['svm'] = LinearSVC(probability=True)
    models['svm'] = SVC(C=0.5, kernel='linear', probability=True)
    #models['gbdt'] = GradientBoostingClassifier(n_estimators=1000)
    models['xgb'] = XGBClassifier(booster='gblinear', learning_rate=0.01, use_label_encoder=False, eval_metric='logloss', n_estimators=500)
    models['cnn'] = "models"
    return models

def feature_select(models, X, X_test, y):
    selector = SelectFromModel(estimator=models).fit(X, y)
    X_train_select = selector.transform(X)
    X_test_select = selector.transform(X_test)
    return X_train_select, X_test_select

def kfold_training(name, models, X, y, X_test, y_test, cv):
    train_pred_set = []
    test_pred_set = []
    train_true_set = []
    X, X_test = data_processing(X, X_test)
    if name == 'cnn':
        X_reshape = X.reshape(X.shape[0],X.shape[1],1)
        X_test_reshape = X_test.reshape(X_test.shape[0],X_test.shape[1],1) 
        for k, (train, valid) in enumerate(cv.split(X, y)):
            model = create_model(X.shape[1])
            model.fit(X_reshape[train], y[train], batch_size=1, epochs=10)
            train_pred_y = model.predict(X_reshape[valid]).flatten()
            test_pred_y = model.predict(X_test_reshape).flatten()
            train_true_set.extend(y[valid])
            train_pred_set.extend(train_pred_y)
            test_pred_set.append(test_pred_y)
    else:
        X, X_test = feature_select(models, X, X_test, y)
        for k, (train, valid) in enumerate(cv.split(X, y)):
            model = models.fit(X[train], y[train])
            train_pred_y = model.predict_proba(X[valid])[:,1]
            train_true_set.extend(y[valid])
            test_pred_y = model.predict_proba(X_test)[:,1]
            train_pred_set.extend(train_pred_y)
            test_pred_set.append(test_pred_y)

    X_train_proba = train_pred_set
    X_test_proba = np.array(test_pred_set).mean(axis=0).tolist()
    y_train_true = train_true_set            
    return X_train_proba, X_test_proba, y_train_true
    
def get_stacking(X_train, y_train, X_test, y_test, random_seed):
    
    X_train_level1 = []
    X_test_level1 = []
    models = get_models()
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=random_seed)

    for name, models in models.items():
        X_train_proba, X_test_proba, y_train_true = kfold_training(name=name, models=models, X=X_train, y=y_train, X_test=X_test, y_test=y_test, cv=cv)
        X_train_level1.append(X_train_proba)
        X_test_level1.append(X_test_proba)
    
    X_train_level1_array = np.array(X_train_level1).T
    X_test_level1_array = np.array(X_test_level1).T
    y_train_true = np.array(y_train_true)
    return X_train_level1_array, X_test_level1_array, y_train_true

def stacking_final_predict(X_train_level1, y_train_true, X_test_level1, y_test):
    auc_report = []
    
    X_all_train = X_train_level1
    X_all_test = X_test_level1
    
    #final_estimator = LogisticRegression(C=0.5, solver='newton-cg', max_iter=500).fit(X_all_train, y_train_true)
    final_estimator = XGBClassifier(booster='gblinear', learning_rate=0.001, use_label_encoder=False, eval_metric='logloss', n_estimators=500).fit(X_all_train, y_train_true)        
        # final_estimator = XGBClassifier(learning_rate=0.05, max_depth=8, n_estimators=500, use_label_encoder=False, eval_metric='logloss', random_state=3).fit(X_all_train[train], y_train_true[train])
    
    y_pred = final_estimator.predict(X_all_test)
    y_pred_proba = final_estimator.predict_proba(X_all_test)[:,1]
    auc = roc_auc_score(y_test, y_pred_proba)
    report = classification_report(y_test, y_pred, output_dict=True)

    report_0 = list(report['0'].values())
    report_1 = list(report['1'].values())

    auc_report.append(auc)
    auc_report.extend(report_0)
    auc_report.extend(report_1)
    print(auc_report)
    return auc_report


def model_select(X_train_level1, y_train_true):
    model_auc = []
    for i in range(4):
        y_pred_proba = X_train_level1[:, i]
        #y_pred = (y_pred_proba >= 0.5).astype(int)
        auc = roc_auc_score(y_train_true, y_pred_proba)
        #report = classification_report(y_train_true, y_pred, output_dict=True)
        model_auc.append(auc)
        #print("第 %d 个模型" % i)
        #print("auc: %f" % auc)
        #print(report['0'].values())
        #print(report['1'].values())
    model_auc_array = np.array(model_auc)
    greatest_model = np.argmax(model_auc_array)
    return greatest_model

def take_out(X_train, X_test, gm):
    X_train_best = X_train[:, gm].reshape(-1,1)
    X_test_best = X_test[:, gm].reshape(-1,1)
    return X_train_best, X_test_best

In [3]:
path = 'data/TFN/'
X_s = pd.read_csv(path + 's_data.csv')
X_f = pd.read_csv(path + 'f_data.csv')
X_t = pd.read_csv(path + 't_data.csv')
X_sf = pd.read_csv(path + 'sf_data.csv')
X_st = pd.read_csv(path + 'st_data.csv')
X_ft = pd.read_csv(path + 'ft_data.csv')
X_stf = pd.read_csv(path + 'stf_data.csv')

X_test_s = pd.read_csv(path + 's_test_data.csv')
X_test_f = pd.read_csv(path + 'f_test_data.csv')
X_test_t = pd.read_csv(path + 't_test_data.csv')
X_test_sf = pd.read_csv(path + 'sf_test_data.csv')
X_test_st = pd.read_csv(path + 'st_test_data.csv')
X_test_ft = pd.read_csv(path + 'ft_test_data.csv')
X_test_stf = pd.read_csv(path + 'stf_test_data.csv')

y = pd.read_csv(path + 'default.csv')
y_test = pd.read_csv(path + 'default_test.csv')


In [4]:
X_s, X_test_s = X_s.values, X_test_s.values
X_f, X_test_f = X_f.values, X_test_f.values
X_t, X_test_t = X_t.values, X_test_t.values
X_sf, X_test_sf = X_sf.values, X_test_sf.values
X_st, X_test_st = X_st.values, X_test_st.values
X_ft, X_test_ft = X_ft.values, X_test_ft.values
X_stf, X_test_stf = X_stf.values, X_test_stf.values
y = y.values.ravel()
y_test = y_test.values.ravel()

In [7]:
def random_replicate(X_f, X_test_f, X_t, X_test_t, X_ft, X_test_ft, X_s, X_test_s, X_sf, X_test_sf, X_st, X_test_st, X_stf, X_test_stf, y, y_test):
    results_replicate = []
    for i in range(100):
        X_train_level1_s, X_test_level1_s, y_train_true_s = get_stacking(X_s, y, X_test_s, y_test, random_seed=i)
        X_train_level1_f, X_test_level1_f, y_train_true_f = get_stacking(X_f, y, X_test_f, y_test, random_seed=i)
        X_train_level1_t, X_test_level1_t, y_train_true_t = get_stacking(X_t, y, X_test_t, y_test, random_seed=i)
        X_train_level1_ft, X_test_level1_ft, y_train_true_ft = get_stacking(X_ft, y, X_test_ft, y_test, random_seed=i)
        X_train_level1_sf, X_test_level1_sf, y_train_true_sf = get_stacking(X_sf, y, X_test_sf, y_test, random_seed=i)
        X_train_level1_st, X_test_level1_st, y_train_true_st = get_stacking(X_st, y, X_test_st, y_test, random_seed=i)
        X_train_level1_stf, X_test_level1_stf, y_train_true_stf = get_stacking(X_stf, y, X_test_stf, y_test, random_seed=i)
        gm_s = model_select(X_test_level1_s, y_test)
        gm_f = model_select(X_test_level1_f, y_test)
        gm_t = model_select(X_test_level1_t, y_test)
        gm_ft = model_select(X_test_level1_ft, y_test)
        gm_sf = model_select(X_test_level1_sf, y_test)
        gm_st = model_select(X_test_level1_st, y_test)
        gm_stf = model_select(X_test_level1_stf, y_test)
        best_train_level_s, best_test_level_s = take_out(X_train_level1_s, X_test_level1_s, gm_s)
        best_train_level_f, best_test_level_f = take_out(X_train_level1_f, X_test_level1_f, gm_f)
        best_train_level_t, best_test_level_t = take_out(X_train_level1_t, X_test_level1_t, gm_t)
        best_train_level_ft, best_test_level_ft = take_out(X_train_level1_ft, X_test_level1_ft, gm_ft)
        best_train_level_sf, best_test_level_sf = take_out(X_train_level1_sf, X_test_level1_sf, gm_sf)
        best_train_level_st, best_test_level_st = take_out(X_train_level1_st, X_test_level1_st, gm_st)
        best_train_level_stf, best_test_level_stf = take_out(X_train_level1_stf, X_test_level1_stf, gm_stf)
        X_train_level1_best = np.concatenate([best_train_level_s, best_train_level_f, best_train_level_t, best_train_level_ft, best_train_level_sf, best_train_level_st, best_train_level_stf], axis=1)
        X_test_level1_best = np.concatenate([best_test_level_s, best_test_level_f, best_test_level_t, best_test_level_ft, best_test_level_sf, best_test_level_st, best_test_level_stf], axis=1)
#auc_best, report_best = stacking_final_predict(X_train_level1_best, X_stf, y_train_true_stf, X_test_level1_best, X_test_stf, y_test)
        auc_report_best = stacking_final_predict(X_train_level1_best, y_train_true_stf, X_test_level1_best, y_test)
        results_replicate.append(auc_report_best)
    results_df = pd.DataFrame(results_replicate, columns=['auc','legit_prec','legit_rec','legit_f1','legit_num','fraud_prec','fraud_rec','fraud_f1','fraud_num'])
    return results_df
    

In [8]:
results_df = random_replicate(X_f, X_test_f, X_t, X_test_t, X_ft, X_test_ft, X_s, X_test_s, X_sf, X_test_sf, X_st, X_test_st, X_stf, X_test_stf, y, y_test)


Epoch 1/10
478/478 [==============================] - 1s 2ms/step - loss: 0.6157 - accuracy: 0.5992
Epoch 2/10
478/478 [==============================] - 1s 2ms/step - loss: 0.5112 - accuracy: 0.7395
Epoch 3/10
478/478 [==============================] - 1s 1ms/step - loss: 0.4627 - accuracy: 0.7582
Epoch 4/10
478/478 [==============================] - 1s 1ms/step - loss: 0.4475 - accuracy: 0.7807
Epoch 5/10
478/478 [==============================] - 1s 1ms/step - loss: 0.4516 - accuracy: 0.7781
Epoch 6/10
478/478 [==============================] - 1s 1ms/step - loss: 0.3331 - accuracy: 0.8777
Epoch 7/10
478/478 [==============================] - 1s 1ms/step - loss: 0.3305 - accuracy: 0.8777
Epoch 8/10
478/478 [==============================] - 1s 1ms/step - loss: 0.2961 - accuracy: 0.8887
Epoch 9/10
478/478 [==============================] - 1s 1ms/step - loss: 0.2634 - accuracy: 0.9072
Epoch 10/10
478/478 [==============================] - 1s 1ms/step - loss: 0.2183 - accuracy: 0.9152

478/478 [==============================] - 1s 3ms/step - loss: 0.6802 - accuracy: 0.5606
Epoch 4/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6699 - accuracy: 0.5930
Epoch 5/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6688 - accuracy: 0.5663
Epoch 6/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6599 - accuracy: 0.5759
Epoch 7/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6497 - accuracy: 0.6065
Epoch 8/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6539 - accuracy: 0.5798
Epoch 9/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6443 - accuracy: 0.6292
Epoch 10/10
478/478 [==============================] - 1s 3ms/step - loss: 0.6136 - accuracy: 0.6593
Epoch 1/10
478/478 [==============================] - 2s 3ms/step - loss: 0.7269 - accuracy: 0.4834
Epoch 2/10
478/478 [==============================] - 1s 3ms/step - loss: 0.7033 - accuracy: 0.5725
Epoch 3/10

Epoch 5/10
479/479 [==============================] - 1s 2ms/step - loss: 0.5235 - accuracy: 0.7287
Epoch 6/10
479/479 [==============================] - 1s 2ms/step - loss: 0.5206 - accuracy: 0.7259
Epoch 7/10
479/479 [==============================] - 1s 2ms/step - loss: 0.4755 - accuracy: 0.7399
Epoch 8/10
479/479 [==============================] - 1s 2ms/step - loss: 0.5448 - accuracy: 0.7193
Epoch 9/10
479/479 [==============================] - 1s 2ms/step - loss: 0.5128 - accuracy: 0.7330
Epoch 10/10
479/479 [==============================] - 1s 2ms/step - loss: 0.4729 - accuracy: 0.7563
Epoch 1/10
478/478 [==============================] - 2s 3ms/step - loss: 0.6700 - accuracy: 0.6374
Epoch 2/10
478/478 [==============================] - 1s 3ms/step - loss: 0.5788 - accuracy: 0.6520
Epoch 3/10
478/478 [==============================] - 1s 3ms/step - loss: 0.5952 - accuracy: 0.7025
Epoch 4/10
478/478 [==============================] - 1s 3ms/step - loss: 0.5618 - accuracy: 0.7379

478/478 [==============================] - 1s 1ms/step - loss: 0.5939 - accuracy: 0.7338
Epoch 7/10
478/478 [==============================] - 1s 1ms/step - loss: 0.5632 - accuracy: 0.7090
Epoch 8/10
478/478 [==============================] - 1s 1ms/step - loss: 0.5303 - accuracy: 0.7163
Epoch 9/10
478/478 [==============================] - 1s 1ms/step - loss: 0.3910 - accuracy: 0.8234
Epoch 10/10
478/478 [==============================] - 1s 1ms/step - loss: 0.3738 - accuracy: 0.8544
Epoch 1/10
478/478 [==============================] - 1s 1ms/step - loss: 0.6989 - accuracy: 0.5486
Epoch 2/10
478/478 [==============================] - 1s 1ms/step - loss: 0.6387 - accuracy: 0.6308
Epoch 3/10
478/478 [==============================] - 1s 1ms/step - loss: 0.6365 - accuracy: 0.6027
Epoch 4/10
478/478 [==============================] - 1s 1ms/step - loss: 0.6435 - accuracy: 0.6137
Epoch 5/10
478/478 [==============================] - 1s 1ms/step - loss: 0.6315 - accuracy: 0.6218
Epoch 6/10

Epoch 8/10
479/479 [==============================] - 1s 3ms/step - loss: 0.1187 - accuracy: 0.9490
Epoch 9/10
479/479 [==============================] - 1s 3ms/step - loss: 0.1099 - accuracy: 0.9673
Epoch 10/10
479/479 [==============================] - 1s 3ms/step - loss: 0.0760 - accuracy: 0.9759
Epoch 1/10
479/479 [==============================] - 2s 3ms/step - loss: 0.5053 - accuracy: 0.7709
Epoch 2/10
479/479 [==============================] - 1s 3ms/step - loss: 0.2872 - accuracy: 0.8842
Epoch 3/10
479/479 [==============================] - 1s 3ms/step - loss: 0.2243 - accuracy: 0.9191
Epoch 4/10
479/479 [==============================] - 1s 3ms/step - loss: 0.2198 - accuracy: 0.9245
Epoch 5/10
479/479 [==============================] - 1s 3ms/step - loss: 0.1573 - accuracy: 0.9493
Epoch 6/10
479/479 [==============================] - 1s 3ms/step - loss: 0.1564 - accuracy: 0.9447
Epoch 7/10
479/479 [==============================] - 1s 3ms/step - loss: 0.1407 - accuracy: 0.9461

...

Epoch 3/10
479/479 [==============================] - 2s 4ms/step - loss: 0.5745 - accuracy: 0.7004
Epoch 4/10
479/479 [==============================] - 2s 4ms/step - loss: 0.5151 - accuracy: 0.7502
Epoch 5/10
479/479 [==============================] - 2s 4ms/step - loss: 0.5364 - accuracy: 0.7293
Epoch 6/10
479/479 [==============================] - 2s 4ms/step - loss: 0.4874 - accuracy: 0.7939
Epoch 7/10
479/479 [==============================] - 2s 4ms/step - loss: 0.5334 - accuracy: 0.7276
Epoch 8/10
479/479 [==============================] - 2s 4ms/step - loss: 0.4564 - accuracy: 0.7611
Epoch 9/10
479/479 [==============================] - 2s 4ms/step - loss: 0.4641 - accuracy: 0.7830
Epoch 10/10
479/479 [==============================] - 2s 4ms/step - loss: 0.4480 - accuracy: 0.8013
[0.82806396484375, 0.9027777777777778, 0.5078125, 0.65, 128, 0.657608695652174, 0.9453125, 0.7756410256410257, 128]
Epoch 1/10
478/478 [==============================] - 1s 2ms/step - loss: 0.6203 - 

478/478 [==============================] - 2s 3ms/step - loss: 0.6520 - accuracy: 0.5829
Epoch 5/10
478/478 [==============================] - 2s 3ms/step - loss: 0.6659 - accuracy: 0.5502
Epoch 6/10
478/478 [==============================] - 2s 3ms/step - loss: 0.6415 - accuracy: 0.6178
Epoch 7/10
478/478 [==============================] - 2s 4ms/step - loss: 0.6346 - accuracy: 0.6541
Epoch 8/10
478/478 [==============================] - 2s 3ms/step - loss: 0.6501 - accuracy: 0.6209
Epoch 9/10
478/478 [==============================] - 2s 4ms/step - loss: 0.6001 - accuracy: 0.6588
Epoch 10/10
478/478 [==============================] - 2s 3ms/step - loss: 0.5914 - accuracy: 0.6667
Epoch 1/10
478/478 [==============================] - 2s 3ms/step - loss: 0.7477 - accuracy: 0.5033
Epoch 2/10
478/478 [==============================] - 2s 4ms/step - loss: 0.6939 - accuracy: 0.5917
Epoch 3/10
478/478 [==============================] - 2s 3ms/step - loss: 0.6864 - accuracy: 0.5676
Epoch 4/10

Epoch 6/10
479/479 [==============================] - 1s 3ms/step - loss: 0.4909 - accuracy: 0.7510
Epoch 7/10
479/479 [==============================] - 1s 2ms/step - loss: 0.4919 - accuracy: 0.7358
Epoch 8/10
479/479 [==============================] - 1s 2ms/step - loss: 0.4876 - accuracy: 0.7415
Epoch 9/10
479/479 [==============================] - 1s 2ms/step - loss: 0.4932 - accuracy: 0.7351
Epoch 10/10
479/479 [==============================] - 1s 2ms/step - loss: 0.4835 - accuracy: 0.7656
Epoch 1/10
479/479 [==============================] - 2s 2ms/step - loss: 0.6015 - accuracy: 0.6581
Epoch 2/10
479/479 [==============================] - 1s 3ms/step - loss: 0.5508 - accuracy: 0.6865
Epoch 3/10
479/479 [==============================] - 1s 3ms/step - loss: 0.5160 - accuracy: 0.7109
Epoch 4/10
479/479 [==============================] - 1s 3ms/step - loss: 0.5463 - accuracy: 0.6907
Epoch 5/10
479/479 [==============================] - 1s 3ms/step - loss: 0.5233 - accuracy: 0.7379

479/479 [==============================] - 1s 2ms/step - loss: 0.2994 - accuracy: 0.8778
Epoch 8/10
479/479 [==============================] - 1s 2ms/step - loss: 0.3080 - accuracy: 0.8905
Epoch 9/10
479/479 [==============================] - 1s 2ms/step - loss: 0.2352 - accuracy: 0.9094
Epoch 10/10
479/479 [==============================] - 1s 2ms/step - loss: 0.2231 - accuracy: 0.9060
Epoch 1/10
478/478 [==============================] - 1s 2ms/step - loss: 0.7010 - accuracy: 0.4771
Epoch 2/10
478/478 [==============================] - 1s 2ms/step - loss: 0.6621 - accuracy: 0.6336
Epoch 3/10
478/478 [==============================] - 1s 2ms/step - loss: 0.6410 - accuracy: 0.6274
Epoch 4/10
478/478 [==============================] - 1s 2ms/step - loss: 0.6195 - accuracy: 0.6273
Epoch 5/10
478/478 [==============================] - 1s 2ms/step - loss: 0.5900 - accuracy: 0.6713
Epoch 6/10
478/478 [==============================] - 1s 2ms/step - loss: 0.5724 - accuracy: 0.6605
Epoch 7/10

478/478 [==============================] - 1s 3ms/step - loss: 0.5380 - accuracy: 0.6863
Epoch 10/10
478/478 [==============================] - 1s 2ms/step - loss: 0.4997 - accuracy: 0.7356
Epoch 1/10
478/478 [==============================] - 2s 2ms/step - loss: 0.5665 - accuracy: 0.7396
Epoch 2/10
478/478 [==============================] - 1s 3ms/step - loss: 0.5406 - accuracy: 0.6726
Epoch 3/10
478/478 [==============================] - 1s 3ms/step - loss: 0.5168 - accuracy: 0.7123
Epoch 4/10
478/478 [==============================] - 1s 2ms/step - loss: 0.5431 - accuracy: 0.7384
Epoch 5/10
478/478 [==============================] - 1s 2ms/step - loss: 0.4963 - accuracy: 0.7555
Epoch 6/10
478/478 [==============================] - 1s 2ms/step - loss: 0.4848 - accuracy: 0.7745
Epoch 7/10
478/478 [==============================] - 1s 2ms/step - loss: 0.5014 - accuracy: 0.7551
Epoch 8/10
478/478 [==============================] - 1s 2ms/step - loss: 0.5210 - accuracy: 0.7291
Epoch 9/10

In [8]:
print(results_df)

        auc  legit_prec  legit_rec  legit_f1  legit_num  fraud_prec  \
0  0.833557    0.902778   0.507812  0.650000        128    0.657609   
1  0.824707    0.904110   0.515625  0.656716        128    0.661202   
2  0.831970    0.904110   0.515625  0.656716        128    0.661202   

   fraud_rec  fraud_f1  fraud_num  
0   0.945312  0.775641        128  
1   0.945312  0.778135        128  
2   0.945312  0.778135        128  
